# Tensorflow with GPU

This notebook provides an introduction to computing on a [GPU](https://cloud.google.com/gpu) in Colab. In this notebook you will connect to a GPU, and then run some basic TensorFlow operations on both the CPU and a GPU, observing the speedup provided by using the GPU.


## Enabling and testing the GPU

First, you'll need to enable GPUs for the notebook:

- Navigate to Edit→Notebook Settings
- select GPU from the Hardware Accelerator drop-down

Next, we'll confirm that we can connect to the GPU with tensorflow:

In [6]:
import tensorflow as tf
device_name = tf.test.gpu_device_name()
if device_name != '/device:GPU:0':
  raise SystemError('GPU device not found')
print('Found GPU at: {}'.format(device_name))

Found GPU at: /device:GPU:0


## Observe TensorFlow speedup on GPU relative to CPU

This example constructs a typical convolutional neural network layer over a
random image and manually places the resulting ops on either the CPU or the GPU
to compare execution speed.

In [7]:
import tensorflow as tf
import timeit

device_name = tf.test.gpu_device_name()
if device_name != '/device:GPU:0':
  print(
      '\n\nThis error most likely means that this notebook is not '
      'configured to use a GPU.  Change this in Notebook Settings via the '
      'command palette (cmd/ctrl-shift-P) or the Edit menu.\n\n')
  raise SystemError('GPU device not found')

def cpu():
  with tf.device('/cpu:0'):
    random_image_cpu = tf.random.normal((100, 100, 100, 3))
    net_cpu = tf.keras.layers.Conv2D(32, 7)(random_image_cpu)
    return tf.math.reduce_sum(net_cpu)

def gpu():
  with tf.device('/device:GPU:0'):
    random_image_gpu = tf.random.normal((100, 100, 100, 3))
    net_gpu = tf.keras.layers.Conv2D(32, 7)(random_image_gpu)
    return tf.math.reduce_sum(net_gpu)

# We run each op once to warm up; see: https://stackoverflow.com/a/45067900
cpu()
gpu()

# Run the op several times.
print('Time (s) to convolve 32x7x7x3 filter over random 100x100x100x3 images '
      '(batch x height x width x channel). Sum of ten runs.')
print('CPU (s):')
cpu_time = timeit.timeit('cpu()', number=10, setup="from __main__ import cpu")
print(cpu_time)
print('GPU (s):')
gpu_time = timeit.timeit('gpu()', number=10, setup="from __main__ import gpu")
print(gpu_time)
print('GPU speedup over CPU: {}x'.format(int(cpu_time/gpu_time)))

Time (s) to convolve 32x7x7x3 filter over random 100x100x100x3 images (batch x height x width x channel). Sum of ten runs.
CPU (s):
3.533890097999972
GPU (s):
0.08478006799998639
GPU speedup over CPU: 41x


In [8]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [28]:
from keras.src import Model
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Embedding, LSTM, Dense, Dropout
from tensorflow.keras.optimizers import Adam
import string

In [29]:
dataset = pd.read_csv("/content/drive/MyDrive/Language_Detection.csv")

In [30]:
dataset.head()

Text Language
0   Nature, in the broadest sense, is the natural...  English
1  "Nature" can refer to the phenomena of the phy...  English
2  The study of nature is a large, if not the onl...  English
3  Although humans are part of nature, human acti...  English
4  [1] The word nature is borrowed from the Old F...  English

In [18]:
#Clean the text data from punctuation signs and convert to lower letter
def clean(text):
  for p in string.punctuation:
    text = text.replace(p, '')
  text = text.lower()
  return (text)
text = dataset['Text'].apply(clean)
text.head(12)


0      nature in the broadest sense is the natural p...
1     nature can refer to the phenomena of the physi...
2     the study of nature is a large if not the only...
3     although humans are part of nature human activ...
4     1 the word nature is borrowed from the old fre...
5     2 in ancient philosophy natura is mostly used ...
6     34 \nthe concept of nature as a whole the phys...
7     during the advent of modern scientific method ...
8     56 with the industrial revolution nature incre...
9     however a vitalist vision of nature closer to ...
10    1 within the various uses of the word today na...
11    nature can refer to the general realm of livin...
Name: Text, dtype: object

In [19]:
#Invoke the tokenizer
tokenizer = Tokenizer()
tokenizer.fit_on_texts(text)

In [20]:
from io import TextIOBase
#Fit the tokenizer
processed_text = tokenizer.texts_to_sequences(text)

In [21]:
processed_text

[[82, 7, 3, 10983, 5884, 21, 3, 673, 2610, 1336, 965, 112, 2611],
 [82, 147, 7816, 13, 3, 10984, 8, 3, 2610, 965, 10, 228, 13, 318, 7, 699],
 [3, 752, 8, 82, 21, 2, 1251, 255, 197, 3, 511, 454, 8, 575],
 [1252,
  2612,
  90,
  454,
  8,
  82,
  576,
  7817,
  21,
  700,
  4755,
  40,
  2,
  3378,
  3972,
  144,
  263,
  673,
  10984],
 [336,
  3,
  400,
  82,
  21,
  10985,
  144,
  3,
  7818,
  5885,
  82,
  10,
  21,
  10986,
  144,
  3,
  2613,
  400,
  2117,
  112,
  7819,
  18068,
  18069,
  10987,
  10,
  7,
  10988,
  1070,
  10989,
  18070,
  18071],
 [729,
  7,
  10988,
  4756,
  2117,
  21,
  3379,
  401,
  40,
  3,
  2613,
  5886,
  8,
  3,
  18072,
  400,
  18073,
  10990,
  183,
  3380,
  1071,
  13,
  3,
  18074,
  7820,
  32,
  1932,
  1639,
  10,
  263,
  1144,
  8,
  3,
  965,
  4757,
  8,
  355,
  2354,
  10991],
 [1772,
  3,
  1933,
  8,
  82,
  40,
  2,
  3973,
  3,
  2610,
  2611,
  21,
  288,
  8,
  785,
  18075,
  8,
  3,
  1253,
  18076,
  115,
  3381,
  122,
  

In [24]:
#characte level tokenization
tokenizer = Tokenizer (char_level = True)
tokenizer.fit_on_texts(dataset['Text'])

In [26]:
chartokens = tokenizer.texts_to_sequences(dataset['Text'])

In [27]:
chartokens

[[1,
  5,
  3,
  7,
  12,
  8,
  2,
  18,
  1,
  4,
  5,
  1,
  7,
  17,
  2,
  1,
  23,
  8,
  6,
  3,
  10,
  2,
  9,
  7,
  1,
  9,
  2,
  5,
  9,
  2,
  18,
  1,
  4,
  9,
  1,
  7,
  17,
  2,
  1,
  5,
  3,
  7,
  12,
  8,
  3,
  11,
  18,
  1,
  15,
  17,
  28,
  9,
  4,
  13,
  3,
  11,
  18,
  1,
  14,
  3,
  7,
  2,
  8,
  4,
  3,
  11,
  1,
  27,
  6,
  8,
  11,
  10,
  1,
  6,
  8,
  1,
  12,
  5,
  4,
  19,
  2,
  8,
  9,
  2,
  20],
 [137,
  5,
  3,
  7,
  12,
  8,
  2,
  137,
  1,
  13,
  3,
  5,
  1,
  8,
  2,
  22,
  2,
  8,
  1,
  7,
  6,
  1,
  7,
  17,
  2,
  1,
  15,
  17,
  2,
  5,
  6,
  14,
  2,
  5,
  3,
  1,
  6,
  22,
  1,
  7,
  17,
  2,
  1,
  15,
  17,
  28,
  9,
  4,
  13,
  3,
  11,
  1,
  27,
  6,
  8,
  11,
  10,
  18,
  1,
  3,
  5,
  10,
  1,
  3,
  11,
  9,
  6,
  1,
  7,
  6,
  1,
  11,
  4,
  22,
  2,
  1,
  4,
  5,
  1,
  16,
  2,
  5,
  2,
  8,
  3,
  11,
  20],
 [7,
  17,
  2,
  1,
  9,
  7,
  12,
  10,
  28,
  1,
  6,
  22,
  1,
  5,
  3,
  7,
